## FaceNet single-predictor models
Set of models investigating face perception:
- single-predictor model with binary regressor coding for presence of any face (**any_faces**)
- **any_faces** + regressor coding for first appearance face for the first time (**first_time_face**)
- **any_faces** + log of time since last appearance of detected face (mean across faces if more than one are present in the frame, **log_mean_time_since**) 
- **any_faces** + log of time since last appearance of detected face (max across multiple faces, **log_max_time_since**) 
- **any_faces** + log of cumulative time the detected face has been on screen (mean across faces, **log_mean_face_time_cum**)
- **any_faces** + log of cumulative time the detected face has been on screen (max across faces, **log_max_face_time_cum**)

In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
from tools.create import create_set_models
from tools.base import (dump_collection, load_collection, 
                        flatten_collection, compute_metrics,
                        _extract_regressors)
from tools.viz import (plot_regressor, plot_regressor,
                       plot_metrics, plot_contrast_by_dataset, plot_contrast_by_analysis,
                       plot_analysis_grid)
from pyns import Neuroscout
import numpy as np
from matplotlib import pyplot as plt
from pathlib import Path
%matplotlib inline

/home/alejandro/anaconda3/lib/python3.7/site-packages/nilearn/datasets/__init__.py:90: FutureWarning: Fetchers from the nilearn.datasets module will be updated in version 0.9 to return python strings instead of bytes and Pandas dataframes instead of Numpy arrays.
  "Numpy arrays.", FutureWarning)


In [3]:
api = Neuroscout()

## Define predictors and confounds

In [4]:
predictors = [['any_faces']]
other = ['first_time_face', 'log_mean_time_since', 'log_max_time_since', 'log_mean_face_time_cum', 'log_max_face_time_cum']
for p in other:
    predictors.append(['any_faces', p])

In [5]:
predictors

[['any_faces'],
 ['any_faces', 'first_time_face'],
 ['any_faces', 'log_mean_time_since'],
 ['any_faces', 'log_max_time_since'],
 ['any_faces', 'log_mean_face_time_cum'],
 ['any_faces', 'log_max_face_time_cum']]

In [6]:
confounds = ['a_comp_cor_00', 'a_comp_cor_01', 'a_comp_cor_02', 'a_comp_cor_03', 'a_comp_cor_04', 'a_comp_cor_05', 'trans_x', 'trans_y', 'trans_z', 'rot_x', 'rot_y', 'rot_z']

## Create models

In [7]:
# mdict = {}
# for pset in predictors:
#    mdict['+'.join(pset)] = create_set_models(pset, confounds, name='+'.join(pset), datasets=['NaturalisticNeuroimagingDatabase'])

In [8]:
filename = Path('models') / 'facenet.json'

In [581]:
mdict = load_collection(filename)

In [605]:
# dump_collection(mdict, filename)

## Generate reports

In [9]:
for (pred, dataset, task), model in flatten_collection(mdict):
    model.generate_report(run_id=model.runs[0])

In [10]:
for pset in predictors:
    mdict['+'.join(pset)]['Budapest']['movie'].plot_report()

## Inspect regressors

In [8]:
df = _extract_regressors(mdict)

In [ ]:
plot_regressor('distribution', df=df, predictors=other,
               split_by='hue', color=None, aspect=3, hist=None, rug=True)

In [ ]:
plot_regressor('timeseries', df=df, predictors=other,
               split_by='row', height=1.2, aspect=10)

In [11]:
agg_df = compute_metrics(df=df, aggfunc=[np.mean, np.std, np.var])

In [ ]:
plot_metrics(agg_df, metrics=['mean', 'std', 'var'], 
             predictors=other,
             sns_function='barplot', height=3, aspect=1)

## Compile models

In [267]:
for (pred, dataset, task), model in flatten_collection(mdict):
    if model.get_status()['status'] in 'DRAFT':
        model.private = False
        model.push()
        model.compile()
    else:
        if dataset == 'SchematicNarrative':
            print(f'{dataset}, {model.status}, {model.hash_id}')

SchematicNarrative, FAILED, 42d8n
SchematicNarrative, PASSED, 9EdJr
SchematicNarrative, FAILED, foent
SchematicNarrative, FAILED, gc5ta
SchematicNarrative, FAILED, hxycu
SchematicNarrative, PASSED, M4jBy
SchematicNarrative, PASSED, MD1LO
SchematicNarrative, PASSED, wJ3Qe
SchematicNarrative, PASSED, Aop4B
SchematicNarrative, PASSED, MpDBj


## Results

In [30]:
flat_models = flatten_collection(mdict)

In [ ]:
plt.rcParams.update({'font.family': 'monospace'})
plot_contrast_by_analysis(flat_models,
                         contrasts=['any_faces'],
                         vmax=10, display_mode='z', figsize=(12,15),
                         threshold=1.96, colorbar=False)

No image for NaturalisticNeuroimagingDatabase
No image for NaturalisticNeuroimagingDatabase
No image for NaturalisticNeuroimagingDatabase
No image for NaturalisticNeuroimagingDatabase
No image for NaturalisticNeuroimagingDatabase
No image for NaturalisticNeuroimagingDatabase
No image for NaturalisticNeuroimagingDatabase
No image for NaturalisticNeuroimagingDatabase
No image for NaturalisticNeuroimagingDatabase
No image for NaturalisticNeuroimagingDatabase


KeyboardInterrupt: 

# FaceNet -- face switch

In [91]:
preds = ['first_time_face', 'log_max_time_since', 'any_faces']

In [92]:
transformations = [
    {
        'Input': ['log_max_time_since', 'first_time_face'],
        'Name': 'ToDense',
        'SamplingRate': 2
        
    },
    {
        'Input': ['log_max_time_since'],
        'Name': 'Threshold',
        'Threshold': 0.5,
        'Binarize': True,
        'Output': ['time_since_temp']
        
    },
    {
        'Input': ['time_since_temp', 'first_time_face'],
        'Output': 'face_switch',
        'Name': 'Or',
    },
    {
        'Input': ['any_faces', 'face_switch'],
        'Name': 'Convolve'
    }
]

In [ ]:
# mdict['any_faces+face_switch'] = create_set_models(predictors=preds, confounds=confounds, name='any_faces+face_switch', transformations=transformations)

In [33]:
for _, an in flatten_collection(mdict['any_faces+face_switch']):
    an.model['Steps'][0]['Model']['X'] = ['face_switch', 'any_faces',
         'a_comp_cor_00',
         'a_comp_cor_01',
         'a_comp_cor_02',
         'a_comp_cor_03',
         'a_comp_cor_04',
         'a_comp_cor_05',
         'trans_x',
         'trans_y',
         'trans_z',
         'rot_x',
         'rot_y',
         'rot_z'
    ]
    an.model['Steps'][0]['DummyContrasts']['Conditions'] = ['face_switch', 'any_faces']
    an.model['Steps'][0]['Transformations'] = transformations
    an.push()

In [37]:
an.plot_report()

In [67]:
for task, analysis in mdict['any_faces+face_switch']['NaturalisticNeuroimagingDatabase'].items():
    analysis.model['Steps'][0]['Model']['X'] = ['face_switch', 'any_faces']
    analysis.push()

In [69]:
for (dataset, task), model in flatten_collection(mdict['any_faces+face_switch']):
    if model.get_status()['status'] in 'DRAFT':
        model.private = False
        model.push()
        model.compile()
    else:
        print(f'{dataset}, {model.status}, {model.hash_id}')

Budapest, PASSED, oz3xu
LearningTemporalStructure, PASSED, netzj
Raiders, PASSED, 65n52
Sherlock, PASSED, 94392
SherlockMerlin, PASSED, 3w236
SherlockMerlin, PASSED, 88dgm
studyforrest, PASSED, a7n6w


In [575]:
# Finished
' '.join([m.hash_id for (dataset, task), m in flatten_collection(mdict['any_faces+face_switch']) 
          if m.get_status()['status'] == 'PASSED' and m.get_uploads()])

'oz3xu netzj edz7x pfcso aqure k8shj p9stc 6q46q 78f5d fvbjz qi8bw 9u7oo 65n52 94392 3w236 88dgm a7n6w'

In [576]:
' '.join([m.hash_id for (dataset, task), m in flatten_collection(mdict['any_faces+face_switch']) 
          if m.get_status()['status'] == 'PASSED' and not m.get_uploads() and
          dataset != 'NaturalisticNeuroimagingDatabase'])

'foent'

In [455]:
' '.join([m.hash_id for (dataset, task), m in flatten_collection(mdict['any_faces+face_switch']) 
          if m.get_status()['status'] == 'PASSED' and not m.get_uploads()
         and dataset == 'NaturalisticNeuroimagingDatabase' and task not in ['citizenfour', '500daysofsummer']])

# Ran w/ 4 cpus--- next one ran w/ 5

''

In [456]:
' '.join([m.hash_id for (dataset, task), m in flatten_collection(mdict['any_faces+face_switch']) 
          if m.get_status()['status'] == 'PASSED' and not m.get_uploads()
         and dataset == 'NaturalisticNeuroimagingDatabase' and task in ['citizenfour', '500daysofsummer']])

''

# All Model

In [577]:
all_name = 'any_faces+face_switch+log_mean_time_since+first_time_face+log_mean_face_time_cum'
transformations = [
    {
        'Input': ['log_mean_time_since', 'first_time_face'],
        'Name': 'ToDense',
        'SamplingRate': 2
        
    },
    {
        'Input': ['log_mean_time_since'],
        'Name': 'Threshold',
        'Threshold': 0.5,
        'Binarize': True,
        'Output': ['time_since_temp']
        
    },
    {
        'Input': ['time_since_temp', 'first_time_face'],
        'Output': 'face_switch',
        'Name': 'Or',
    },
    {
        'Input': ['any_faces', 'face_switch', 'first_time_face', 'log_mean_time_since', 'log_mean_face_time_cum'],
        'Name': 'Convolve'
    }
]

all_preds = ['first_time_face', 'log_mean_time_since', 'any_faces', 'log_mean_face_time_cum']
# mdict[all_name] = create_set_models(
#     predictors=all_preds, confounds=confounds, name=name, transformations=transformations)

In [227]:
for (dataset, task), an in flatten_collection(mdict[all_name]):
    if dataset != 'NaturalisticNeuroimagingDatabase':
        all_inputs = all_preds + ['face_switch'] + confounds
    else:
        all_inputs = all_preds + ['face_switch']
    an.model['Steps'][0]['Model']['X'] = all_inputs
    an.model['Steps'][0]['DummyContrasts']['Conditions'] = all_inputs
    an.model['Steps'][0]['Transformations'] = transformations
    an.push()

In [228]:
m = mdict[all_name]['NaturalisticNeuroimagingDatabase']['12yearsaslave']
m.generate_report(run_id=m.runs[2])

{'generated_at': '2021-11-08T22:0',
 'result': None,
 'sampling_rate': None,
 'scale': False,
 'status': 'PENDING',
 'traceback': None,
 'warnings': []}

In [493]:
for (dataset, task), model in flatten_collection(mdict[all_name]):
    if model.get_status()['status'] in 'DRAFT':
        model.compile()
    else:
        print(f'{dataset}, {model.status}, {model.hash_id}')

Budapest, PASSED, s7pj7
LearningTemporalStructure, PASSED, oof8g
NaturalisticNeuroimagingDatabase, PASSED, 8vrcd
NaturalisticNeuroimagingDatabase, PASSED, 6k8uz
NaturalisticNeuroimagingDatabase, PASSED, ik4bx
NaturalisticNeuroimagingDatabase, PASSED, bkasx
NaturalisticNeuroimagingDatabase, PASSED, fur4j
NaturalisticNeuroimagingDatabase, PASSED, hs5n6
NaturalisticNeuroimagingDatabase, PASSED, ijnzw
NaturalisticNeuroimagingDatabase, PASSED, jgafo
NaturalisticNeuroimagingDatabase, PASSED, c2hgs
NaturalisticNeuroimagingDatabase, PASSED, 6bspy
Raiders, PASSED, ksx3m
SchematicNarrative, PASSED, hxycu
Sherlock, PASSED, 6srd2
SherlockMerlin, PENDING, 9sio9
SherlockMerlin, PASSED, oej5q
studyforrest, PASSED, 5hu2n


In [509]:
# Finished
' '.join([m.hash_id for (dataset, task), m in flatten_collection(mdict[all_name]) 
          if m.get_status()['status'] == 'PASSED' and m.get_uploads()])

's7pj7 8vrcd 6k8uz ik4bx bkasx fur4j hs5n6 ijnzw 6bspy ksx3m hxycu 6srd2 oej5q 5hu2n'

In [578]:
' '.join([m.hash_id for (dataset, task), m in flatten_collection(mdict[all_name]) 
          if m.get_status()['status'] == 'PASSED' and not m.get_uploads() and
          dataset != 'NaturalisticNeuroimagingDatabase'
         and len(m.runs) < 30])

'9sio9'

In [579]:
' '.join([m.hash_id for (dataset, task), m in flatten_collection(mdict[all_name]) 
          if m.get_status()['status'] == 'PASSED' and not m.get_uploads()
         and dataset == 'NaturalisticNeuroimagingDatabase' and task not in ['citizenfour', '500daysofsummer']])

''

In [475]:
' '.join([m.hash_id for (dataset, task), m in flatten_collection(mdict[all_name]) 
          if m.get_status()['status'] == 'PASSED' and not m.get_uploads()
         and dataset == 'NaturalisticNeuroimagingDatabase' and task in ['citizenfour', '500daysofsummer']])

''

### face_switch + time_cum + speech + shot_change

In [582]:
all_speech_shot_name = '+'.join(hrf_vars)
hrf_vars = ['speech', 'shot_change','face_switch', 'log_mean_face_time_cum']
transformations = [
    {
        'Input': ['log_mean_time_since', 'first_time_face'],
        'Name': 'ToDense',
        'SamplingRate': 2
        
    },
    {
        'Input': ['log_mean_time_since'],
        'Name': 'Threshold',
        'Threshold': 0.5,
        'Binarize': True,        
    },
    {
        'Input': ['log_mean_time_since', 'first_time_face'],
        'Output': 'face_switch',
        'Name': 'Or',
    },
    {
        'Input': hrf_vars,
        'Name': 'Convolve'
    }
]

input_preds = ['first_time_face', 'log_mean_time_since', 'log_mean_face_time_cum', 'shot_change', 'speech']
# mdict[all_speech_shot_name] = create_set_models(
#     predictors=input_preds, confounds=confounds, name=all_speech_shot_name, transformations=transformations)

In [583]:
for (dataset, task), an in flatten_collection(mdict[all_speech_shot_name]):
    an.model['Steps'][0]['Model']['X'] = hrf_vars + confounds
    an.model['Steps'][0]['DummyContrasts']['Conditions'] = hrf_vars
    an.model['Steps'][0]['Transformations'] = transformations
    an.push()

In [ ]:
for (dataset, task), model in flatten_collection(mdict[all_speech_shot_name]):
    if model.get_status()['status'] in 'DRAFT':
        model.private = False
        model.push()
        model.compile()
    else:
        print(f'{dataset}, {model.status}, {model.hash_id}')

### anyfaces + above

In [584]:
hrf_vars = ['any_faces', 'speech', 'shot_change','face_switch', 'log_mean_face_time_cum']
name = '+'.join(hrf_vars)
transformations = [
    {
        'Input': ['log_mean_time_since', 'first_time_face'],
        'Name': 'ToDense',
        'SamplingRate': 2
        
    },
    {
        'Input': ['log_mean_time_since'],
        'Name': 'Threshold',
        'Threshold': 0.5,
        'Binarize': True,        
    },
    {
        'Input': ['log_mean_time_since', 'first_time_face'],
        'Output': 'face_switch',
        'Name': 'Or',
    },
    {
        'Input': hrf_vars,
        'Name': 'Convolve'
    }
]

input_preds = ['any_faces', 'first_time_face', 'log_mean_time_since', 'log_mean_face_time_cum', 'shot_change', 'speech']
# mdict[name] = create_set_models(
#     predictors=input_preds, confounds=confounds, name=name, transformations=transformations)

for (dataset, task), an in flatten_collection(mdict[name]):
    an.model['Steps'][0]['Model']['X'] = hrf_vars + confounds
    an.model['Steps'][0]['DummyContrasts']['Conditions'] = hrf_vars
    an.model['Steps'][0]['Transformations'] = transformations
    an.push()

In [496]:
for (dataset, task), model in flatten_collection(mdict[name]):
    if model.get_status()['status'] in 'DRAFT':
        model.compile()
    else:
        print(f'{dataset}, {model.status}, {model.hash_id}')

Budapest, PASSED, 5tgye
LearningTemporalStructure, PASSED, ecc36
Raiders, PASSED, 6dtb5
SchematicNarrative, PASSED, j2yjh
Sherlock, PASSED, 35ohj
SherlockMerlin, PASSED, eu357
SherlockMerlin, PASSED, i9q2o


### Notes:

Model w/ too many correlated predictors was less consistent across datasets


Models to run:


- "back up" plan: pairwise models including speech, and face_switch + shot change

- face_switch + time_since + first_timeface (lower priority)


## any_faces + speech + shot_change

In [585]:
hrf_vars = ['any_faces', 'speech', 'shot_change']
name = '+'.join(hrf_vars)

# mdict[name] = create_set_models(
#     predictors=hrf_vars, confounds=confounds, name=name)

In [586]:
# for (dataset, task), model in flatten_collection(mdict[name]):
#     if model.get_status()['status'] in 'DRAFT':
#         model.compile()
#     else:
#         print(f'{dataset}, {model.status}, {model.hash_id}')

In [587]:
' '.join([m.hash_id for (dataset, task), m in flatten_collection(mdict[name]) 
          if m.get_status()['status'] == 'PASSED' and not m.get_uploads()
         and len(m.runs) > 30])

''

In [588]:
' '.join([m.hash_id for (dataset, task), m in flatten_collection(mdict[name]) 
          if m.get_status()['status'] == 'PASSED' and not m.get_uploads()
         and len(m.runs) < 30])

''

## any_faces + speech + shot_change + face_switch

In [589]:
hrf_vars = ['any_faces', 'speech', 'shot_change','face_switch']
name = '+'.join(hrf_vars)
transformations = [
    {
        'Input': ['log_mean_time_since', 'first_time_face'],
        'Name': 'ToDense',
        'SamplingRate': 2
        
    },
    {
        'Input': ['log_mean_time_since'],
        'Name': 'Threshold',
        'Threshold': 0.5,
        'Binarize': True,        
    },
    {
        'Input': ['log_mean_time_since', 'first_time_face'],
        'Output': 'face_switch',
        'Name': 'Or',
    },
    {
        'Input': hrf_vars,
        'Name': 'Convolve'
    }
]

input_preds = ['any_faces', 'first_time_face', 'log_mean_time_since', 'shot_change', 'speech']
# mdict[name] = create_set_models(
#     predictors=input_preds, confounds=confounds, name=name, transformations=transformations)

# for (dataset, task), an in flatten_collection(mdict[name]):
#     an.model['Steps'][0]['Model']['X'] = hrf_vars + confounds
#     an.model['Steps'][0]['DummyContrasts']['Conditions'] = hrf_vars
#     an.model['Steps'][0]['Transformations'] = transformations
#     an.push()

In [569]:
for (dataset, task), model in flatten_collection(mdict[name]):
    if model.get_status()['status'] in 'DRAFT':
        model.compile()
    else:
        print(f'{dataset}, {model.status}, {model.hash_id}')

Budapest, PASSED, dzyva
LearningTemporalStructure, PENDING, iu3g9
Raiders, PASSED, nvei3
SchematicNarrative, PASSED, k6j2o
Sherlock, PASSED, 46gc6
SherlockMerlin, PASSED, bsx6g
SherlockMerlin, PASSED, b8jq2


In [590]:
' '.join([m.hash_id for (dataset, task), m in flatten_collection(mdict[name]) 
          if m.get_status()['status'] == 'PASSED' and not m.get_uploads()
         and len(m.runs) > 30])

'iu3g9 nvei3'

In [591]:
' '.join([m.hash_id for (dataset, task), m in flatten_collection(mdict[name]) 
          if m.get_status()['status'] == 'PASSED' and not m.get_uploads()
         and len(m.runs) < 30])

''

# any_faces + shot_change + speech + time_cum

In [600]:
hrf_vars = ['any_faces', 'speech', 'shot_change','log_mean_face_time_cum']
name = '+'.join(hrf_vars)

# mdict[name] = create_set_models(
#     predictors=hrf_vars, confounds=confounds, name=name)

In [601]:
name

'any_faces+speech+shot_change+log_mean_face_time_cum'

In [602]:
for (dataset, task), model in flatten_collection(mdict[name]):
    if model.get_status()['status'] in 'DRAFT':
        model.compile()
    else:
        print(f'{dataset}, {model.status}, {model.hash_id}')

Budapest, PASSED, h57v2
LearningTemporalStructure, PASSED, oyndv
Raiders, PASSED, ggic7
SchematicNarrative, PASSED, n3pj7
Sherlock, PASSED, nyb95
SherlockMerlin, PASSED, dci4u
SherlockMerlin, PASSED, ovbpo


In [603]:
' '.join([m.hash_id for (dataset, task), m in flatten_collection(mdict[name]) 
          if m.get_status()['status'] == 'PASSED' and not m.get_uploads()
         and len(m.runs) > 30])

''

In [604]:
' '.join([m.hash_id for (dataset, task), m in flatten_collection(mdict[name]) 
          if m.get_status()['status'] == 'PASSED' and not m.get_uploads()
         and len(m.runs) < 30])

''